# References

# Modified from KEFE's preprocess_review.py

In [1]:
!python --version
!pwd

Python 3.8.5


'pwd' is not recognized as an internal or external command,
operable program or batch file.


In [2]:
from utils import *
from pprint import pprint

import ssl
ssl._create_default_https_context = ssl._create_unverified_context

config = get_config('config.yaml')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\enlik\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


# Read Input

## Bolt (Both Apple App Store and Google Play Store

In [3]:
df = read_csv_from_gdrive(config['csv_input']['bolt_google'])
total_reviews = len(df)
unique_users  = len(df['userName'].unique())
unknown_users = len(df[df['userName']=='A Google user'])
mean = df['score'].mean()

print(f'Total English reviews: {total_reviews} \n')
print(f'Total unique users : {unique_users}')
print(f'Total unknown users: {unknown_users}')
print(f'Total users who gave multiple reviews: {total_reviews - unique_users - unknown_users}\n')
print(f'Average rating for this app based on the textual reviews: {round(mean,2)} \n')

Total English reviews: 51907 

Total unique users : 46872
Total unknown users: 4780
Total users who gave multiple reviews: 255

Average rating for this app based on the textual reviews: 3.96 



In [4]:
# df2 = read_csv_from_gdrive(config['csv_input']['bolt_apple'])
df2 = pd.read_csv('')
total_reviews = len(df2)
unique_users  = len(df2['userName'].unique())
mean = df2['rating'].mean()

print(f'Total English reviews: {total_reviews} \n')
print(f'Total unique users : {unique_users}')
print(f'Total users who gave multiple reviews: {total_reviews - unique_users}\n')
print(f'Average rating for this app based on the textual reviews: {round(mean,2)} \n')

Total English reviews: 3154 

Total unique users : 3149
Total users who gave multiple reviews: 5

Average rating for this app based on the textual reviews: 3.02 



In [5]:
# merge both apple and google
google = df.content.astype(str)
apple = df2.review.astype(str)
df_merged = google.append(apple, ignore_index=True)
total_reviews = len(df_merged)

print(f'Total English reviews: {total_reviews} \n')

Total English reviews: 55061 



# Preprocessing Input Data

## Remove Non-English User Reviews

In [13]:
df2_test = df2.reset_index(drop=True)
df2_test = df2_test[2900:]
df2_test = df2_test.reset_index(drop=True)
df2_test

userName  isEdited  \
0         violetsant     False   
1              Zirts     False   
2      Max Lazarenko     False   
3    124956163949382     False   
4             EJESTO     False   
..               ...       ...   
249      -Randycool-     False   
250        Jaak Sarv     False   
251        AlexEesti     False   
252             Xfrz     False   
253         dhanenko     False   

                                                review  rating  \
0    The thing that bugs me the most about Taxify i...       3   
1    Bolt is doing good, the app is fast and simple...       4   
2    Good UX. Liked the freshers’ discounts. Liked ...       5   
3    Stood in the cold waiting for taxi, licence 82...       1   
4    Overall good app but one drop of tar ruins it ...       2   
..                                                 ...     ...   
249  Зачем регестрироваться? Я просто хочу посмотре...       1   
250                                                 :)       5   
251  Слишком мало машин, иногда нет вообще, часто п...       2   
252  1. samm: positsioneerime telefoni\n2. samm: "V...       1   
253  Taxify's purpose was that you can CHOOSE your ...       1   

                               title                 date  
0         “There’s no cars near you”  2018-10-15 22:43:49  
1                     Solid taxi app  2019-08-10 15:01:36  
2                          Satisfied  2019-03-07 13:43:47  
3    Drivers can cancel arbitrarily?  2020-05-25 22:20:36  
4             Keeps you on your toes  2019-08-08 01:27:22  
..                               ...                  ...  
249                              мда  2013-09-28 01:46:50  
250               Best taxi app ever  2015-01-17 22:47:46  
251                         Так себе  2013-09-04 18:01:36  
252                       Kasutu app  2013-08-13 05:43:24  
253      New update completely sucks  2017-05-20 10:38:09  

[254 rows x 6 columns]

In [23]:
df_merged[0]

"The first thing I noticed is that you can't prenook your trip which isn't great. As I had to catch a flight at 4 pm today I decided to give it a go anyway using the instant booking. There were 2 drivers available near me and I went to book one of them. Completed the booking only to find that the driver disappeared and he now was shown as engaged. Went to book the other one and same happened again. Unreliable service. I will get rid of the app today"

In [24]:
%%time
listOfNonEnglishIndex = []

for i in range(0, len(df_merged)):
    reviewText = df_merged[i]
    print(reviewText)
    print(isEnglishReview(reviewText))
    print('\n')
    
    isEnglish, listToStr, english_score = isEnglishReview(reviewText)
    if isEnglish == False:
        listOfNonEnglishIndex.append(i)
        

The first thing I noticed is that you can't prenook your trip which isn't great. As I had to catch a flight at 4 pm today I decided to give it a go anyway using the instant booking. There were 2 drivers available near me and I went to book one of them. Completed the booking only to find that the driver disappeared and he now was shown as engaged. Went to book the other one and same happened again. Unreliable service. I will get rid of the app today
(True, 'en:0.9999967473618985', 0.9999967473618985)


Your GPS setting around Cape Town International Airport needs to be looked at. It always take my location to the drop off and go section of the airport when I'm actually about 1km away from that spot. Sometimes the drivers mobile numbers does not match their profile. But other than that, the app is quite user friendly.
(True, 'en:0.9999962714210083', 0.9999962714210083)


I was invited by my friend and was given a £10 free promo to use on my first trip. I tried to use it and it would not 

(True, 'en:0.9999972921039672', 0.9999972921039672)


There prices is errattic discounts of 50%but limited to R30 it's cheaper the uber but still flippen expensive or overpriced and safety isnt high on the table as in the case of this morning the cost rangers between R69 to R111 for a 5min trip that's being plain corrupt(6-12-2020).
(True, 'en:0.9999973272879343', 0.9999973272879343)


To say I am disgusted by this service would be an understatement. I confirmed a ride and was accepted by a bolt driver, who then after 5 minutes registered that he had picked me up despite me still waiting at my pick up location and drive in the opposite direction of where I had set my destination to before "dropping me off" and charging me for it. There was no option to cancel the ride or report the issue properly and afterwards when I attempted to contact customer support I was ignored.
(True, 'en:0.9999940101831127', 0.9999940101831127)


Found cheaper than Uber, but an option to go back and tip drive

The app couldn't pick my location despite the fact that I am on a major street. The address it always show isn't my address.
(True, 'en:0.9999969883602026', 0.9999969883602026)


I am very disappointed with this service. Always when i book they are forever busy a driver just accepted my request and canceled me , this service use to be one of the best but now i wouldn't even wanna even rate ull not even 1star
(True, 'en:0.9999985728304189', 0.9999985728304189)


I have been getting discounts (50% off) but it doesn't not show on the app. Which mean I have to pay the full price whereas I have a discount.
(True, 'en:0.9999964924029006', 0.9999964924029006)


This app is awesome. Ride Fee was great and so were the drivers so far: Kaashief and Tonderai on separate occasions while on my trip in Cape Town, thank you
(True, 'en:0.9999961097610971', 0.9999961097610971)


App has massively improved since it started. Arrival time is more accurate and drivers seem more responsive. Customer service 

(True, 'en:0.9999979017852709', 0.9999979017852709)


Please fix the app, when you are typing the destination, the field gets hidden, it was not always like this
(True, 'en:0.9999987720015591', 0.9999987720015591)


Amazing app I really wish you would stick to the cost u approximate, before the ride it would show like 3200-4100 But 1 might end up paying 6000, Please work on this
(True, 'en:0.9999981070135797', 0.9999981070135797)


Promotions are limited once you request a trip that is far only around your local area they are also not given towards the week of month end Driver sometimes accepts rides while they are still finishing other rides. Other driver don't pick up calls when called on the number according to their info on th app. Nd the app will charge you once you cancel the ride if dissatisfied with the service .
(True, 'en:0.9999965744720972', 0.9999965744720972)


Absolutely convenient and to think I was sceptical at first, but you guys changed my mind so fast. Great customer

Hello, I suggest that you let riders register on the app with a valid photo ID and their real names on the ID to help identify them when there is an issue concerning the drive. Recently there has been issues where some armed robbers disguise themselves as riders and attacked the driver, because of this consider my suggestion and let's work together and save the lives of drivers. #driverlivesmatters
(True, 'en:0.9999977427763053', 0.9999977427763053)


But have bad performing system, wrong pickup/destination, bad maps and poor rating system works on that. Thank You
(True, 'en:0.9999964480751972', 0.9999964480751972)


Got charged almost twice the price on the app all because the drive could n follow the map properly he kept on getting lost im not sure why he did that
(True, 'en:0.9999982813083962', 0.9999982813083962)


I got blocked after my first ride and support can't tell me why. I've been using uber many years with always great reviews. Atleast send me and email or call give me a r

...

(True, 'en:0.9999973701694844', 0.9999973701694844)


Estamos encantados con la aplicación👌🏽
(False, None, 0)


Taxify is Great but must start screening its drivers (background checks) before putting them to work. So far I have had excellent drivers but such loopholes should not exist to avoid the bad name that plagues Uber.
(True, 'en:0.9999961320384245', 0.9999961320384245)


ARIELFERNANDOD9W
(False, None, 0)


Everything is fine as long as you don’t have a problem with them. The taxi driver dropped me off and didn’t close the trip on the app, leading to an extra charge of 3 times the cost of what this trip usually is. Wrote a message to support and more than 2 days after I still do not even have an answer nor a refund. Will probably switch to another app because of the extra charge and the lack of support when something like this happens. Totally not recommended!
(True, 'en:0.999998542415599', 0.999998542415599)


Si no quieres perder tiempo y energía negociando el precio del trayec

(True, 'en:0.9999950857234234', 0.9999950857234234)


Don’t get surprised if your 6 euro ride gets absurdly cancelled right before your rider arrives, then see same ride price is raised up to 12, and when you say “f** it, I need the ride” and push the button see price becomes 14 right before getting the ride.

Best of all, you wont be able to find customer support but some random FAQ that doesn’t really answer your questions.

You were great, used you for years, referred it to people, but this practice is truly way too low. Not ethical. 

It makes me seek new alternatives, and surely there will be other people doing the same.
(True, 'en:0.9999965299616634', 0.9999965299616634)


The title says it all really. The price given when ordering a taxi is only an estimate. They will never charge you less, however about half the time charge you more. The last time I was charged almost 2x the original amount. Will take my money elsewhere, as they can’t be trusted.
(True, 'en:0.9999984341375693',

(True, 'en:0.9999974363187155', 0.9999974363187155)


Easy to use, fast, comfortable. Only had 1 incident when driver didn't find me but the app said he had arrived. Keep up the good work! Väga tublid! :)
(True, 'en:0.9999964588058087', 0.9999964588058087)


I am using Taxify as my first choice everywhere in Europe when available. Great UX, good driver validation, fair cost.
(True, 'en:0.999995366224494', 0.999995366224494)


Looks great, easy to use and very efficient .
(True, 'en:0.9999970749969277', 0.9999970749969277)


When I first used it I was amazed how well it works. I'm impressed. Great app.
(True, 'en:0.9999960323919048', 0.9999960323919048)


95% of the times the drivers are very nice, find me quikly by using the GPS and drive fast but safe. Hea töö kutid👌🏻
(True, 'en:0.9999973585702001', 0.9999973585702001)


Convenient way to get a ride, no need to carry CCs nor cash is a godsend.
(True, 'en:0.9999961593117196', 0.9999961593117196)


Comfortable to use, no crashes, no bug

(False, None, 0)


Väga mugav!
(False, None, 0)


Äpp pakub takso mis veel sõidab eelmist sõitu ja katkestamise soovi eest küsib raha kuigi näitab et veel eelmist klienti sõidutatakse
(False, None, 0)


Kiire ja mugav lahendus punktist A punkti B liikumiseks!
(False, None, 0)


Отличное обслуживание! Быстрая подача машины!
(False, None, 0)


Sõit oli ilus, sile tee, Tallinna tänavad olid korras. Kahjuks juhil eelviimane tööpäev ja rohkem Taxifyd ei kasuta seetõttu 😔
(False, None, 0)


Такое ощущение, что таксисты специально объезжают город Маарду стороной, так как заказать оттуда такси практически невозможно.
(False, None, 0)


Большинство водятелов просто мудаки последнее время, цены за такое обслуживание просто космические, сегодня водитель вообще можно сказать обманул, приехал на место С ДРУГИМ ПАССАЖИРОМ что бы тот снял деньги и отвезти пассажира,  при том что ожидание было 2 минуты написано, а ждал я его минут 10 и после этого ожидания еще и это приключилось.
Берите на работу норм

Верните выбор авто.
(False, None, 0)


Taksofirmad tulid kõik heas usus kaasa ja üheskoos rõõmustati uue innovatiivse lahenduse üle. Nüüd nad on reetnud kõik oma koostööpartnerid. Sisuliselt võtsid ju koostööparnterina kõigi partnerite andmed ja siis pöörasid kogu äri enda kasuks ning hakkasid konkurendiks? Pettus?
(False, None, 0)


Väga mugav ja lihtne kasutada.
(False, None, 0)


При выборе русского языка, остается английский язык.
(False, None, 0)


Классная программка 5+
(False, None, 0)


👍
(False, None, 0)


Tellimine in lihtne ja kiire, saabumise jälgimine mugav.
(False, None, 0)


Great app!
(True, 'en:0.9999948339646532', 0.9999948339646532)


Suurepärane, lihtne ja kiire äpp mida saab iga situatsioonis ja konditsioonis kasutada. Ainult kiidusõnad!
(False, None, 0)


Vägev
(False, None, 0)


Ma olen VÄGA õnnetu, et enam ei näe, kui palju tärne taksojuht on saanud! :( muidu olen endiselt rahul, taxify on olnud asendamatu kaaslane. (iPhone 5S)
(False, None, 0)


Parim viis taks

In [27]:
%%time
df_merged_english = df_merged.drop(df_merged.index[listOfNonEnglishIndex])
total_reviews_before = len(df_merged)
total_reviews_after = len(df_merged_english)
total_non_english_reviews = len(listOfNonEnglishIndex)

print(f'Total reviews (BEFORE): {total_reviews_before} \n')
print(f'Total reviews (AFTER): {total_reviews_after} \n')
print(f'Total Non-English reviews: {total_non_english_reviews} \n')

Total reviews (BEFORE): 55061 

Total reviews (AFTER): 40364 

Total Non-English reviews: 14697 

Wall time: 8.98 ms
